In [2]:
import argparse
import array
import math
import numpy as np
import random
import wave

In [2]:
import librosa

In [1]:
import os ,glob, os.path

In [3]:
def cal_adjusted_rms(clean_rms, snr):
    a = float(snr) / 20
    noise_rms = clean_rms / (10**a)
    return noise_rms

def cal_amp(wf):
    buffer = wf.readframes(wf.getnframes())
    # The dtype depends on the value of pulse-code modulation. The int16 is set for 16-bit PCM.
    amptitude = (np.frombuffer(buffer, dtype="int16")).astype(np.float64)
    return amptitude

def cal_rms(amp):
    return np.sqrt(np.mean(np.square(amp), axis=-1))

def save_waveform(output_path, params, amp):
    output_file = wave.Wave_write(output_path)
    output_file.setparams(params) #nchannels, sampwidth, framerate, nframes, comptype, compname
    output_file.writeframes(array.array('h', amp.astype(np.int16)).tobytes() )
    output_file.close()

In [14]:
os.system('ffmpeg -i ./audio_1.mp4 -acodec pcm_s16le -ac 1 -ar 16000 ./audio_1.wav')

0

In [75]:
audio_list=glob.glob('./olds/f_1/*.wav')
for j,i in enumerate(audio_list):
    clean_file = i
    path = './olds/'
    k= j+1
    name = 'f_5_%s'%k
    noise_file = 'C:/Users/dataedu09/Documents/이동진/workplace/background_sound/PCAFETER/ch09.wav'
    clean_wav = wave.open(clean_file, "r")
    noise_wav = wave.open(noise_file, "r")
    clean_amp = cal_amp(clean_wav)
    noise_amp = cal_amp(noise_wav)
    clean_rms = cal_rms(clean_amp)
    start = random.randint(0, len(noise_amp)-len(clean_amp))
    divided_noise_amp = noise_amp[start: start + len(clean_amp)]
    noise_rms = cal_rms(divided_noise_amp)
    # nosie = -3
    snr = 0
    adjusted_noise_rms = cal_adjusted_rms(clean_rms, snr)
    adjusted_noise_amp = divided_noise_amp * (adjusted_noise_rms / noise_rms) 
    mixed_amp = (clean_amp + adjusted_noise_amp)
    #Avoid clipping noise
    max_int16 = np.iinfo(np.int16).max
    min_int16 = np.iinfo(np.int16).min
    if mixed_amp.max(axis=0) > max_int16 or mixed_amp.min(axis=0) < min_int16:
        if mixed_amp.max(axis=0) >= abs(mixed_amp.min(axis=0)): 
            reduction_rate = max_int16 / mixed_amp.max(axis=0)
        else :
            reduction_rate = min_int16 / mixed_amp.min(axis=0)
        mixed_amp = mixed_amp * (reduction_rate)
        clean_amp = clean_amp * (reduction_rate)

    save_waveform('./olds/%s_1.wav'%name, clean_wav.getparams(), mixed_amp)
    
    snr = -5
    adjusted_noise_rms = cal_adjusted_rms(clean_rms, snr)
    adjusted_noise_amp = divided_noise_amp * (adjusted_noise_rms / noise_rms) 
    mixed_amp = (clean_amp + adjusted_noise_amp)
    #Avoid clipping noise
    max_int16 = np.iinfo(np.int16).max
    min_int16 = np.iinfo(np.int16).min
    if mixed_amp.max(axis=0) > max_int16 or mixed_amp.min(axis=0) < min_int16:
        if mixed_amp.max(axis=0) >= abs(mixed_amp.min(axis=0)): 
            reduction_rate = max_int16 / mixed_amp.max(axis=0)
        else :
            reduction_rate = min_int16 / mixed_amp.min(axis=0)
        mixed_amp = mixed_amp * (reduction_rate)
        clean_amp = clean_amp * (reduction_rate)

    save_waveform('./olds/%s_2.wav'%name, clean_wav.getparams(), mixed_amp)
    
    path2 = './olds/%s_0.wav'%name
    if os.path.isfile(path+str(name)+'_0.wav'):
        pass
    else:
        shutil.copy(i, path2)

In [55]:
clean_file = './audio_1.wav'
noise_file = 'C:/Users/dataedu09/Documents/이동진/workplace/background_sound/PCAFETER/ch01.wav'

In [17]:
clean_wav = wave.open(clean_file, "r")
noise_wav = wave.open(noise_file, "r")

In [35]:
clean_wav.getparams()

_wave_params(nchannels=1, sampwidth=2, framerate=16000, nframes=3199896, comptype='NONE', compname='not compressed')

In [18]:
clean_amp = cal_amp(clean_wav)
noise_amp = cal_amp(noise_wav)

In [30]:
y, sr = librosa.load('./audio_1.wav', sr = 16000)
y, sr

(array([0., 0., 0., ..., 0., 0., 0.], dtype=float32), 16000)

In [34]:
len(y)

3199896

In [32]:
import IPython.display as ipd
a=ipd.Audio(y, rate=sr)
a

In [19]:
print(clean_amp)

[0. 0. 0. ... 0. 0. 0.]


In [20]:
print(noise_amp)

[  0.   0.   0. ... -86. -21.  53.]


In [48]:
print(type(noise_amp))

<class 'numpy.ndarray'>


In [42]:
clean_rms = cal_rms(clean_amp)

start = random.randint(0, len(noise_amp)-len(clean_amp))
divided_noise_amp = noise_amp[start: start + len(clean_amp)]
noise_rms = cal_rms(divided_noise_amp)

snr = 5
adjusted_noise_rms = cal_adjusted_rms(clean_rms, snr)

In [43]:
adjusted_noise_amp = divided_noise_amp * (adjusted_noise_rms / noise_rms) 
mixed_amp = (clean_amp + adjusted_noise_amp)

In [44]:
print(mixed_amp )

[-237.20355385 -207.13549772 -374.18025395 ...  674.86081517  330.74861733
  133.63580498]


In [45]:
print(adjusted_noise_amp)

[-237.20355385 -207.13549772 -374.18025395 ...  674.86081517  330.74861733
  133.63580498]


In [46]:
#Avoid clipping noise
max_int16 = np.iinfo(np.int16).max
min_int16 = np.iinfo(np.int16).min
if mixed_amp.max(axis=0) > max_int16 or mixed_amp.min(axis=0) < min_int16:
    if mixed_amp.max(axis=0) >= abs(mixed_amp.min(axis=0)): 
        reduction_rate = max_int16 / mixed_amp.max(axis=0)
    else :
        reduction_rate = min_int16 / mixed_amp.min(axis=0)
    mixed_amp = mixed_amp * (reduction_rate)
    clean_amp = clean_amp * (reduction_rate)

save_waveform('./1_noise_5db.wav', clean_wav.getparams(), mixed_amp)